In [3]:
library(dplyr)
library(stringr)
library(readr)
library(tidyr)
library(lfe)
library(glmnet)
library(aod)
library(xgboost)
library(doMC)
registerDoMC(20)


Attaching package: ‘dplyr’


The following objects are masked from ‘package:stats’:

    filter, lag


The following objects are masked from ‘package:base’:

    intersect, setdiff, setequal, union


Loading required package: Matrix


Attaching package: ‘Matrix’


The following objects are masked from ‘package:tidyr’:

    expand, pack, unpack


Loaded glmnet 3.0-2



Attaching package: ‘xgboost’


The following object is masked from ‘package:dplyr’:

    slice


Loading required package: foreach

Loading required package: iterators

Loading required package: parallel



In [ ]:
### Loading Data
fp <- '/nfs/sloanlab004/projects/covid_mobility_proj/data/'
load(str_c(fp, 'PROCESSED_DATA/county_mobility_dvs.Rdata'))
sci           <- read_delim(str_c(fp, 'fb_social_connectedness/sci_county/county_county_data.tsv'), delim ='\t', col_types = 'ddd')
safegraph     <- read_csv(str_c(fp, 'PROCESSED_DATA/safegraph_social_distancing_aggregate_county.csv'))
counties_long <- read_csv(str_c(fp, 'PROCESSED_DATA/county_policy_long.csv'))
countyInfo    <- read_csv(str_c(fp, 'PROCESSED_DATA/countyInfo.csv'))
weather       <- read_csv(str_c(fp, 'PROCESSED_DATA/county_weather.csv'))
voteShare     <- read_csv(str_c(fp, 'PROCESSED_DATA/county_vote_shares_2016.csv'))
WFH           <- read_csv(str_c(fp, "naics_codes/NAICS_workfromhome.csv")) 
census        <- read_csv(str_c(fp, 'census_data/cc-est2018-alldata.csv'))
naics         <- read_csv(str_c(fp, 'PROCESSED_DATA/safegraph_daily_patterns_2_digit_naics_aggregate_county.csv'))
naics_jan     <- read_csv(str_c(fp, 'PROCESSED_DATA/historic_safegraph/safegraph_daily_patterns_2_digit_naics_aggregate_county_historic_2020-01.csv'))
naics_feb     <- read_csv(str_c(fp, 'PROCESSED_DATA/historic_safegraph/safegraph_daily_patterns_2_digit_naics_aggregate_county_historic_2020-02.csv'))
fb            <- read_csv(str_c(fp, 'PROCESSED_DATA/fb_mobility.csv'))

In [ ]:
# Clean weather data

weather %>%
    mutate(county_fips = as.numeric(county_fips)) %>%
    rename(ds = dt) -> weather

weather %>%
    inner_join(weather %>%
               group_by(county_fips) %>%
               tally() %>%
               filter(n == max(n)) %>%
               select(-n)) -> weather

In [ ]:
# Create different weights to weight data points in the model
# However, based on our testing, weights generally worsens F stat, so we do not use weights in current models

# census weights 
census %>% filter(YEAR==11) %>% 
    filter(AGEGRP == 0) %>% 
    mutate(county_fips = as.numeric(paste0(STATE, COUNTY))) %>% 
    select(county_fips, TOT_POP) %>% 
    mutate(w_pop = TOT_POP/sum(TOT_POP)) -> temp_census

# device count weights
safegraph %>% 
    group_by(county_fips) %>% 
    summarise(max_device_count = max(device_count), 
              mean_device_count = mean(device_count)) -> n_df
n_df %>% 
    mutate(norm_max_device = max_device_count/sum(max_device_count), 
           norm_mean_device = mean_device_count/sum(mean_device_count)) -> n_df

In [ ]:
# clean up work from home index data
WFH %>% 
    mutate(NAICS = as.character(NAICS), 
           NAICS_TITLE = as.character(NAICS_TITLE)) -> WFH
add_wfh <- data.frame(NAICS = c(31, 32, 33, 44, 45, 48, 49), 
                      NAICS_TITLE = c(rep("Manufacturing", 3), "Retail Trade", "Retail Trade",
                                      "Transportation and Warehousing", "Transportation and Warehousing"))
add_wfh %>% 
    left_join(WFH, by = 'NAICS_TITLE') %>% 
    select(-NAICS.y) %>% 
    mutate(NAICS_TITLE = as.character(NAICS_TITLE)) -> add_wfh
colnames(add_wfh)[1] = "NAICS"
wfh <- rbind(WFH, add_wfh)

In [ ]:
# create local baseline - share
naics_baseline = bind_rows(naics_jan, naics_feb) %>% 
    group_by(county_fips, two_digit_naics) %>%
    summarise(visit_count = sum(raw_visit_count, na.rm=TRUE)) 

naics_baseline %>% group_by(county_fips) %>% summarise(sum_visit_count = sum(visit_count)) %>% 
    right_join(naics_baseline, by = 'county_fips') %>% 
    mutate(baseline_ratio = visit_count / sum_visit_count) %>% 
    select(county_fips, two_digit_naics, baseline_ratio) %>% filter(!is.na(county_fips)) %>% 
    spread(two_digit_naics, baseline_ratio, fill = 0)-> naics_baseline


# # I originally wanted to create another version of shift, but given the time constraint, I decided to use the other version (next)
# naics_national_daily = naics %>% group_by(date, two_digit_naics) %>%
#     summarise(visit_count = sum(raw_visit_count))
# naics_national_daily %>% group_by(date) %>% 
#     summarise(sum_visit_count = sum(visit_count)) %>%
#     right_join(naics_national_daily, by = 'date') %>% 
#     mutate(national_ratio = visit_count / sum_visit_count) %>% 
#     select(date, two_digit_naics, national_ratio) %>%
#     spread(two_digit_naics, national_ratio, fill = 0) -> naics_national_daily

# create national shock - shift: percent change relative to the baseline
naics_national_change = naics %>% group_by(date, two_digit_naics) %>%
    summarise(visit_count = sum(raw_visit_count))

naics_national_change2 = bind_rows(naics_jan, naics_feb) %>% 
    group_by(date, two_digit_naics) %>% 
    summarise(daily_visit = sum(raw_visit_count, na.rm=TRUE)) %>% 
    group_by(two_digit_naics) %>% 
    summarise(mean_visit = mean(daily_visit, na.rm=TRUE)) %>%
    right_join(naics_national_change, by = c('two_digit_naics')) %>% 
    mutate(percent_change = (visit_count - mean_visit) / mean_visit) 

naics_national_change2 %>% select(two_digit_naics, date, percent_change) %>%
    spread(two_digit_naics, percent_change, fill = 0) -> naics_national_change

for (i in 2:ncol(naics_national_change)){
    naics_code = colnames(naics_national_change)[i]
    colnames(naics_national_change)[i] = paste0('national_percent_change', naics_code)
}

# create national shock - shift: log change 
# In this case, we don’t actually have to take the difference from baseline because of the fixed effects
naics_national_logchange = naics %>% group_by(date, two_digit_naics) %>%
    summarise(visit_count = sum(raw_visit_count)) %>%
    mutate(log_visit = log(visit_count + 1)) 

naics_national_logchange %>% select(two_digit_naics, date, log_visit) %>%
    spread(two_digit_naics, log_visit, fill = 0) -> naics_national_logchange

for (i in 2:ncol(naics_national_logchange)){
    naics_code = colnames(naics_national_logchange)[i]
    colnames(naics_national_logchange)[i] = paste0('national_logchange', naics_code)
}

In [ ]:
# Code for "full" safegraph data...
#sci %>% 
#    select(county_fips = user_county) %>% 
#    distinct() %>%
#    inner_join(safegraph %>% 
#               select(county_fips) %>% 
#               distinct()) %>% 
#    inner_join(weather %>%
#               select(county_fips) %>%
#               distinct()) -> fips
#
#expand.grid(fips$county_fips, unique(safegraph$ds)) %>%
#    rename(county_fips = Var1, ds = Var2) %>%
#    filter(ds >= as.Date('2020-03-01'), ds <= as.Date('2020-04-18')) %>%
#    left_join(safegraph) %>%
#    group_by(county_fips) %>%
#    summarize(n = sum(is.na(completely_home_device_count))) %>%
#    filter(n > 0)

In [ ]:
### Data Preprocessing
census %>% 
  filter(YEAR == 11) %>% 
  filter(AGEGRP==0) %>%
  group_by(STATE, COUNTY) %>% 
  summarise(n = sum(TOT_POP)) %>% 
  ungroup() %>%
  mutate(COUNTY = as.numeric(str_c(STATE, COUNTY))) %>%
  rename(county_fips = COUNTY) %>% 
  select(-STATE) -> population

counties_long %>% 
    mutate(value = 1) %>%
    spread(key = type, value = value) -> countyPolicy

safegraph %>%
    group_by(county_fips) %>%
    summarize(n = n()) %>%
    filter(n == max(n)) %>%
    select(county_fips) %>%
    inner_join(sci %>% 
               ungroup() %>% 
               select(county_fips = user_county) %>% 
               distinct()) %>%
    inner_join(countyPolicy %>% 
               select(county_fips = fips) %>% 
               distinct()) %>%
    semi_join(weather %>% 
              select(county_fips) %>% 
              distinct()) %>%
    semi_join(fb %>%
              group_by(county_fips) %>%
              tally() %>%
              filter(n == max(n))) -> fips

write_csv(fips, str_c(fp, 'PROCESSED_DATA/fipsList.csv'))

In [ ]:
safegraph %>%
    inner_join(fips) %>%
    arrange(county_fips, ds) %>%
    inner_join(countyInfo %>% select(-county_name)) %>%
    mutate(nhd     = 1 - completely_home_device_count/device_count,
           ash_nhd = asinh(nhd)) %>%
    select(ds, county_fips, nhd, ash_nhd, state_abbv) %>%
    left_join(countyPolicy, by = c('ds' = 'dt', 'county_fips' = 'fips', 'state_abbv')) %>%
    group_by(county_fips) %>%
    arrange(county_fips, ds) %>%
    fill(gatherings50, gatherings500, gyms_movies, restaurants, schools, stay_home) %>%
    replace_na(list(gatherings50 = 0, gatherings500 = 0, 
                    gyms_movies = 0, restaurants = 0, 
                    schools = 0, stay_home = 0)) %>%
    select(-name) %>%
    left_join(weather)%>%
    # based on the most updated disucssion, we limit the analysis period to be 3/1-4/18.
    filter(ds >= as.Date('2020-03-01')) %>% 
    filter(ds <= as.Date('2020-04-18')) %>% 
    left_join(fb) %>%
    mutate(rnstu     = 1 - fb_rstu,
           ash_rnstu = asinh(rnstu)) %>% 
    rename(btvrc = fb_btvrc) %>%
    select(-fb_rstu) %>%
    inner_join(population) %>%
    left_join(naics_national_change, by = c('ds' = 'date')) %>%
    left_join(naics_baseline, by = 'county_fips') %>% 
    left_join(naics_national_logchange, by = c('ds' = 'date')) %>%
    left_join(county_mobility_dvs, by = c('county_fips' = 'origin_county', 'ds')) %>%
    mutate(mcbgv     = (non_home_cbg_visits_within_county + cbg_visits_outside_county + home_cbg_visits)/device_count,
           log_mcbgv = log(mcbgv)) %>%
    rowwise() %>%
    mutate(ban_gmr = ifelse(stay_home == 1, 0, max(gyms_movies, restaurants))) %>%
    ungroup() -> df

df %>%
    ungroup() %>%
    select(ds) %>%
    distinct() %>%
    arrange(ds) -> dates


# when joining with naics visit data, there will be NA produced because there are missing data 
#         for some counties and some industries. So I set all these missing data to be 0.
df[is.na(df)]=0
head(df)

In [ ]:
df %>% 
    mutate(shiftshare_11 = national_percent_change11 * `11`,
           shiftshare_21 = national_percent_change21 * `21`,
           shiftshare_22 = national_percent_change22 * `22`,
           shiftshare_23 = national_percent_change23 * `23`,
           shiftshare_31 = national_percent_change31 * `31`,
           shiftshare_32 = national_percent_change32 * `32`,
           shiftshare_33 = national_percent_change33 * `33`,
           shiftshare_42 = national_percent_change42 * `42`,
           shiftshare_44 = national_percent_change44 * `44`,
           shiftshare_45 = national_percent_change45 * `45`,
           shiftshare_48 = national_percent_change48 * `48`,
           shiftshare_49 = national_percent_change49 * `49`,
           shiftshare_51 = national_percent_change51 * `51`,
           shiftshare_52 = national_percent_change52 * `52`,
           shiftshare_53 = national_percent_change53 * `53`,
           shiftshare_54 = national_percent_change54 * `54`,
           shiftshare_55 = national_percent_change55 * `55`,
           shiftshare_56 = national_percent_change56 * `56`,
           shiftshare_61 = national_percent_change61 * `61`,
           shiftshare_62 = national_percent_change62 * `62`,
           shiftshare_71 = national_percent_change71 * `71`,
           shiftshare_72 = national_percent_change72 * `72`,
           shiftshare_81 = national_percent_change81 * `81`,
           shiftshare_92 = national_percent_change92 * `92`,
           shiftshare_NA = `national_percent_change<NA>` * `<NA>`) -> df

In [ ]:
#foreach(i = c('11', '21', '22', '23', '31', '32', '33', '42', '44', '45', '48', '49', '51', '52', '53', '54', '55', '56', '61', '62', '71', '72', '81', '92', 'NA'), .combine = c) %do%
#cor(df[[str_c('shiftshare1_',i)]], df[[str_c('shiftshare2_',i)]])

In [ ]:
df %>%
    select(-X1,
           -matches('national_*'),
           -matches('^[0-9][0-9]$'),
           -`<NA>`,
           -gatherings50,
           -gatherings500,
           -gyms_movies,
           -restaurants,
           -schools,
           -non_home_cbg_visits_within_county,
           -cbg_visits_outside_county,
           -home_cbg_visits,
           -device_count,
           -outside_device_county_visits) %>%
    arrange(ds, county_fips) -> df

In [ ]:
df %>%
    ungroup() %>%
    select(ds, county_fips, PRCP, TMAX) %>%
    mutate(pq = ntile(PRCP, 20), 
           tq = ntile(TMAX, 20)) -> weather_quantiles

wq_ind <- function(thres) {
    weather_quantiles %>%
        transmute(tempname1 = as.numeric(pq >= thres),
                  tempname2 = as.numeric(tq >= thres)) -> temp
    colnames(temp) <- c(str_c('prcp', str_pad(thres, 2, pad = '0')), str_c('tmax', str_pad(thres, 2, pad = '0'))) 
    return(temp)
}

wq_inds <- foreach(i = 2:20, .combine = cbind) %dopar% wq_ind(i)

min.nonzero.pq <- weather_quantiles %>%
    group_by(pq) %>%
    summarize(PRCP = sum(PRCP)) %>%
    filter(PRCP > 0) %>%
    summarize(pq = min(pq))
min.nonzero.pq <- min.nonzero.pq$pq

wq_colnames <- c(str_c('prcp', str_pad(min.nonzero.pq:20, 2, pad = '0')), str_c('tmax', str_pad(2:20, 2, pad = '0')))

df %>%
    bind_cols(wq_inds[wq_colnames]) -> df
wq_inds[wq_colnames] %>% write_csv(str_c(fp, '/intermediate_objects/weatherQuantiles.csv'))

In [ ]:
weather_quantiles %>%
    group_by(pq) %>%
    summarize(min = min(PRCP), max = max(PRCP)) %>%
    rename(quantile = pq) %>%
    mutate(var = 'PRCP') -> pq

weather_quantiles %>%
    group_by(tq) %>%
    summarize(min = min(TMAX), max = max(TMAX)) %>%
    rename(quantile = tq) %>%
    mutate(var = 'TMAX') -> tq

bind_rows(pq, tq) %>%
    select(var, quantile, min, max) -> wq
saveRDS(wq, str_c(fp, '/PROCESSED_DATA/weatherQuantileValues.RDS'))

In [ ]:
# clean up sci data
sci %>%
    inner_join(fips, by = c('user_county' = 'county_fips')) %>%
    inner_join(fips, by = c('fr_county' = 'county_fips')) %>%
    left_join(population, by = c('fr_county' = 'county_fips')) %>%
    mutate(w = ifelse(user_county == fr_county, 0 , scaled_sci * n)) %>%
    group_by(user_county) %>%
    mutate(w = w/sum(w)) %>% 
    arrange(user_county, fr_county) -> sci

In [ ]:
# Generating Weighting Matrices
sci %>% 
    select(user_county, fr_county, w) %>%
    spread(key = fr_county, value = w) %>%
    ungroup() %>%
    select(-user_county) %>%
    as.matrix() -> WM

# geo adj matrix, rows are origin county, columns are destination.
load('/nfs/sloanlab004/projects/covid_mobility_proj/data/PROCESSED_DATA/geo_adjacency_matrix.Rdata')
as.data.frame(geo_adj_matrix_bayes_counts) %>%
    mutate(origin_county = rownames(geo_adj_matrix_bayes_counts)) %>%
    gather(key = 'dest_county', value = 'w', -origin_county) %>%
    mutate(origin_county = as.numeric(origin_county),
           dest_county = as.numeric(dest_county),
           w = ifelse(origin_county == dest_county, 0 , w)) %>%
    inner_join(fips, by = c('origin_county' = 'county_fips')) %>%
    inner_join(fips, by = c('dest_county' = 'county_fips')) %>%
    group_by(dest_county) %>%
    mutate(w = w / sum(w)) %>%
    spread(key = origin_county, value = w) %>%
    ungroup() %>%
    select(-dest_county) %>%
    as.matrix() -> gWM

In [ ]:
save(WM,  file = '/nfs/sloanlab004/projects/covid_mobility_proj/data/PROCESSED_DATA/sciWM.RData')
save(gWM, file = '/nfs/sloanlab004/projects/covid_mobility_proj/data/PROCESSED_DATA/geoWM.RData')

In [ ]:
# function that constructs alter covariate vectors
weightedAlters <- function(df, wm, colname) {
    df %>% 
        select(ds, county_fips) %>%
        mutate(var = df[[colname]]) %>%
        spread(key = county_fips, value = var) %>%
        ungroup() %>%
        select(-ds) %>%
        as.matrix() -> txn_data
    
    outMatrix <- tcrossprod(txn_data, wm)
    colnames(outMatrix) <- colnames(txn_data)
    
    data.frame(dates, outMatrix) %>%
        gather(key = 'county_fips', value = 'value', -ds) %>%
        mutate(county_fips = as.integer(str_sub(county_fips, 2, -1))) %>% 
        arrange(ds, county_fips) %>%
        select(-ds, -county_fips) -> out_df
    colnames(out_df)[1] <- str_c('alter_', colname)
    return(out_df)
}

In [ ]:
df %>%
    mutate(nhd_Xsh           = nhd * stay_home,
           ash_nhd_Xsh       = ash_nhd * stay_home,
           btvrc_Xsh         = btvrc * stay_home,
           rnstu_Xsh         = rnstu * stay_home,
           ash_rnstu_Xsh     = ash_rnstu * stay_home,
           mcbgv_Xsh         = mcbgv * stay_home,
           log_mcbgv_Xsh     = log_mcbgv * stay_home,
           shiftshare_11_Xsh = shiftshare_11 * stay_home,
           shiftshare_21_Xsh = shiftshare_21 * stay_home,
           shiftshare_22_Xsh = shiftshare_22 * stay_home,
           shiftshare_23_Xsh = shiftshare_23 * stay_home,
           shiftshare_31_Xsh = shiftshare_31 * stay_home,
           shiftshare_32_Xsh = shiftshare_32 * stay_home,
           shiftshare_33_Xsh = shiftshare_33 * stay_home,
           shiftshare_42_Xsh = shiftshare_42 * stay_home,
           shiftshare_44_Xsh = shiftshare_44 * stay_home,
           shiftshare_45_Xsh = shiftshare_45 * stay_home,
           shiftshare_48_Xsh = shiftshare_48 * stay_home,
           shiftshare_49_Xsh = shiftshare_49 * stay_home,
           shiftshare_51_Xsh = shiftshare_51 * stay_home,
           shiftshare_52_Xsh = shiftshare_52 * stay_home,
           shiftshare_53_Xsh = shiftshare_53 * stay_home,
           shiftshare_54_Xsh = shiftshare_54 * stay_home,
           shiftshare_55_Xsh = shiftshare_55 * stay_home,
           shiftshare_56_Xsh = shiftshare_56 * stay_home,
           shiftshare_61_Xsh = shiftshare_61 * stay_home,
           shiftshare_62_Xsh = shiftshare_62 * stay_home,
           shiftshare_71_Xsh = shiftshare_71 * stay_home,
           shiftshare_72_Xsh = shiftshare_72 * stay_home,
           shiftshare_81_Xsh = shiftshare_81 * stay_home,
           shiftshare_92_Xsh = shiftshare_92 * stay_home,
           shiftshare_NA_Xsh = shiftshare_NA * stay_home,
           prcp10_Xsh        = prcp10 * stay_home,
           prcp11_Xsh        = prcp11 * stay_home,
           prcp12_Xsh        = prcp12 * stay_home,
           prcp13_Xsh        = prcp13 * stay_home,
           prcp14_Xsh        = prcp14 * stay_home,
           prcp15_Xsh        = prcp15 * stay_home,
           prcp16_Xsh        = prcp16 * stay_home,
           prcp17_Xsh        = prcp17 * stay_home,
           prcp18_Xsh        = prcp18 * stay_home,
           prcp19_Xsh        = prcp19 * stay_home,
           prcp10_Xsh        = prcp20 * stay_home,
           tmax02_Xsh        = tmax02 * stay_home,
           tmax03_Xsh        = tmax03 * stay_home,
           tmax04_Xsh        = tmax04 * stay_home,
           tmax05_Xsh        = tmax05 * stay_home,
           tmax06_Xsh        = tmax06 * stay_home,
           tmax07_Xsh        = tmax07 * stay_home,
           tmax08_Xsh        = tmax08 * stay_home,
           tmax09_Xsh        = tmax09 * stay_home,
           tmax10_Xsh        = tmax10 * stay_home,
           tmax11_Xsh        = tmax11 * stay_home,
           tmax12_Xsh        = tmax12 * stay_home,
           tmax13_Xsh        = tmax13 * stay_home,
           tmax14_Xsh        = tmax14 * stay_home,
           tmax15_Xsh        = tmax15 * stay_home,
           tmax16_Xsh        = tmax16 * stay_home,
           tmax17_Xsh        = tmax17 * stay_home,
           tmax18_Xsh        = tmax18 * stay_home,
           tmax19_Xsh        = tmax19 * stay_home,
           tmax20_Xsh        = tmax20 * stay_home) -> df

In [ ]:
saveRDS(df, file = '/nfs/sloanlab004/projects/covid_mobility_proj/data/PROCESSED_DATA/data_pre_alter.RData')

In [ ]:
df %>%
    select(-ds,
           -county_fips, 
           -state_abbv,
           -n,
           -PRCP,
           -TMAX,
           -matches('[al][so][hg]_')) %>%
    colnames() -> cols_to_alterize
cols_to_alterize

In [ ]:
alters <- foreach(i = 1:length(cols_to_alterize), .combine = cbind) %dopar% 
    weightedAlters(df, WM, cols_to_alterize[i])

In [ ]:
sh_geo_alter   <- weightedAlters(df, gWM, 'stay_home')
bgmr_geo_alter <- weightedAlters(df, gWM, 'ban_gmr')
colnames(sh_geo_alter)   <- 'geo_alter_sh'
colnames(bgmr_geo_alter) <- 'geo_alter_bgmr'

In [ ]:
df %>%
    bind_cols(alters,
              sh_geo_alter,
              bgmr_geo_alter) %>%
    rename(sg_nhd     = nhd,
           sg_mcbgv   = mcbgv,
           fb_rnstu   = rnstu,
           fb_btvrc   = btvrc,
           alter_sh   = alter_stay_home,
           alter_bgmr = alter_ban_gmr) %>%
    mutate(ash_alter_nhd       = asinh(alter_nhd),
           ash_alter_rnstu     = asinh(alter_rnstu),
           log_alter_mcbgv     = log(alter_mcbgv)) %>%
    mutate_at(vars(matches('alter')), .funs = list(X_EgoSH = function(x) x * df$stay_home)) -> panel

In [58]:
saveRDS(panel, file = '/nfs/sloanlab004/projects/covid_mobility_proj/data/PROCESSED_DATA/data_pre_residualization.RData')

In [48]:
panel <- readRDS('/nfs/sloanlab004/projects/covid_mobility_proj/data/PROCESSED_DATA/data_pre_residualization.RData')

In [49]:
# partialing out fixed effects from everything
panel %>%
    ungroup() %>%
    mutate(PRCP.fe.r = felm(PRCP ~ 0 | county_fips + ds, .)$resid,
           TMAX.fe.r = felm(TMAX ~ 0 | county_fips + ds, .)$resid) -> panel

In [51]:
set.seed(2345)
panel %>%
    ungroup() %>%
    select(county_fips) %>%
    distinct() %>%
    mutate(i = sample(1:n(), n(), replace = F),
           grp = i %% 3 + 1) %>%
    select(-i) -> groups

panel %>%
    left_join(groups) -> panel

panel %>%
    select(ds, county_fips, PRCP.fe.r, TMAX.fe.r, n) %>%
    left_join(groups) -> residualizer_df

folds <- list(which(groups$grp %in% 1), 
              which(groups$grp %in% 2), 
              which(groups$grp %in% 3))

XGresidualizer <- function(Y, colname) {
    print(colname)
    residualizer_df %>%
        mutate(Y = Y,
               Y.r = felm(Y ~ 0 | county_fips + ds, .)$resid) -> temp_df
    
    dm    <- xgb.DMatrix(data = model.matrix(~ 0 + PRCP.fe.r + TMAX.fe.r, temp_df), label = temp_df$Y.r)
    param <- list(max_depth=2, eta=.5, silent=1, objective='reg:linear')
    fit   <- xgb.cv(params = param, 
                    data = dm, 
                    folds = folds,
                    nrounds = 100, 
                    early_stopping_rounds = 3, 
                    weight = temp_df$n)
    best_n <- fit$best_iteration
    for (i in 1:3) {
        tr  <- temp_df %>% filter(grp != i)
        trm <- xgb.DMatrix(data = model.matrix(~ 0 + PRCP.fe.r + TMAX.fe.r, tr), label = tr$Y.r)
        fit <- xgb.train(params = param, 
                         data = trm, 
                         nrounds = best_n, 
                         weight = tr$n)
        te  <- temp_df %>% filter(grp == i)
        tem <- xgb.DMatrix(data = model.matrix(~ 0 + PRCP.fe.r + TMAX.fe.r, te), label = te$Y.r)
        te %>%
            select(county_fips, ds) %>%
            mutate(pred = predict(fit, newdata = tem)) -> pred_df
        assign(str_c('temp',i), pred_df)
    }
    out <- bind_rows(temp1, temp2, temp3) %>%
        arrange(ds, county_fips) %>%
        mutate(tempname = temp_df$Y.r - pred) %>%
        select(-pred, -ds, -county_fips)
    colnames(out) <- str_c(colname, '.r')
    return(out)
}

Joining, by = c("county_fips", "grp")

Joining, by = "county_fips"



In [52]:
save(residualizer_df, file = '/nfs/sloanlab004/projects/covid_mobility_proj/data/intermediate_objects/residualizer_df.RData')
save(folds, file = '/nfs/sloanlab004/projects/covid_mobility_proj/data/intermediate_objects/folds.RData')

In [53]:
cols_to_xgr <- colnames(
    panel %>%
         select(
             -ds,
             -county_fips,
             -state_abbv,
             -n,
             -grp,
             -PRCP,
             -TMAX,
             -PRCP.fe.r,
             -TMAX.fe.r,
             -matches('^prcp..$'),
             -matches('^tmax..$')
         )
)
cols_to_xgr

[1] "sg_nhd"                            "ash_nhd"                          
  [3] "stay_home"                         "fb_btvrc"                         
  [5] "fb_rnstu"                          "ash_rnstu"                        
  [7] "sg_mcbgv"                          "log_mcbgv"                        
  [9] "ban_gmr"                           "shiftshare_11"                    
 [11] "shiftshare_21"                     "shiftshare_22"                    
 [13] "shiftshare_23"                     "shiftshare_31"                    
 [15] "shiftshare_32"                     "shiftshare_33"                    
 [17] "shiftshare_42"                     "shiftshare_44"                    
 [19] "shiftshare_45"                     "shiftshare_48"                    
 [21] "shiftshare_49"                     "shiftshare_51"                    
 [23] "shiftshare_52"                     "shiftshare_53"                    
 [25] "shiftshare_54"                     "shiftshare_55"                    
 [27] "shiftshare_56"                     "shiftshare_61"                    
 [29] "shiftshare_62"                     "shiftshare_71"                    
 [31] "shiftshare_72"                     "shiftshare_81"                    
 [33] "shiftshare_92"                     "shiftshare_NA"                    
 [35] "nhd_Xsh"                           "ash_nhd_Xsh"                      
 [37] "btvrc_Xsh"                         "rnstu_Xsh"                        
 [39] "ash_rnstu_Xsh"                     "mcbgv_Xsh"                        
 [41] "log_mcbgv_Xsh"                     "shiftshare_11_Xsh"                
 [43] "shiftshare_21_Xsh"                 "shiftshare_22_Xsh"                
 [45] "shiftshare_23_Xsh"                 "shiftshare_31_Xsh"                
 [47] "shiftshare_32_Xsh"                 "shiftshare_33_Xsh"                
 [49] "shiftshare_42_Xsh"                 "shiftshare_44_Xsh"                
 [51] "shiftshare_45_Xsh"                 "shiftshare_48_Xsh"                
 [53] "shiftshare_49_Xsh"                 "shiftshare_51_Xsh"                
 [55] "shiftshare_52_Xsh"                 "shiftshare_53_Xsh"                
 [57] "shiftshare_54_Xsh"                 "shiftshare_55_Xsh"                
 [59] "shiftshare_56_Xsh"                 "shiftshare_61_Xsh"                
 [61] "shiftshare_62_Xsh"                 "shiftshare_71_Xsh"                
 [63] "shiftshare_72_Xsh"                 "shiftshare_81_Xsh"                
 [65] "shiftshare_92_Xsh"                 "shiftshare_NA_Xsh"                
 [67] "prcp10_Xsh"                        "prcp11_Xsh"                       
 [69] "prcp12_Xsh"                        "prcp13_Xsh"                       
 [71] "prcp14_Xsh"                        "prcp15_Xsh"                       
 [73] "prcp16_Xsh"                        "prcp17_Xsh"                       
 [75] "prcp18_Xsh"                        "prcp19_Xsh"                       
 [77] "tmax02_Xsh"                        "tmax03_Xsh"                       
 [79] "tmax04_Xsh"                        "tmax05_Xsh"                       
 [81] "tmax06_Xsh"                        "tmax07_Xsh"                       
 [83] "tmax08_Xsh"                        "tmax09_Xsh"                       
 [85] "tmax10_Xsh"                        "tmax11_Xsh"                       
 [87] "tmax12_Xsh"                        "tmax13_Xsh"                       
 [89] "tmax14_Xsh"                        "tmax15_Xsh"                       
 [91] "tmax16_Xsh"                        "tmax17_Xsh"                       
 [93] "tmax18_Xsh"                        "tmax19_Xsh"                       
 [95] "tmax20_Xsh"                        "alter_nhd"                        
 [97] "alter_sh"                          "alter_btvrc"                      
 [99] "alter_rnstu"                       "alter_mcbgv"                      
[101] "alter_bgmr"                        "alter_shiftshare_11"              
[103] "alter_shiftshare_

In [54]:
xg.residuals <- foreach(i = 1:length(cols_to_xgr), .combine = cbind) %do% XGresidualizer(panel[[cols_to_xgr[i]]], cols_to_xgr[i])
panel %>%
    bind_cols(xg.residuals) -> panel

[1] "sg_nhd"
[1]	train-rmse:0.252465+0.000291	test-rmse:0.252463+0.001321 
Multiple eval metrics are present. Will use test_rmse for early stopping.
Will train until test_rmse hasn't improved in 3 rounds.

[2]	train-rmse:0.129630+0.000209	test-rmse:0.129651+0.001644 
[3]	train-rmse:0.070919+0.000192	test-rmse:0.070995+0.001806 
[4]	train-rmse:0.045486+0.000230	test-rmse:0.045747+0.001649 
[5]	train-rmse:0.036335+0.000280	test-rmse:0.036702+0.001349 
[6]	train-rmse:0.033589+0.000290	test-rmse:0.034077+0.001023 
[7]	train-rmse:0.032805+0.000313	test-rmse:0.033341+0.000809 
[8]	train-rmse:0.032517+0.000292	test-rmse:0.033144+0.000744 
[9]	train-rmse:0.032365+0.000268	test-rmse:0.033129+0.000706 
[10]	train-rmse:0.032252+0.000271	test-rmse:0.033125+0.000643 
[11]	train-rmse:0.032164+0.000327	test-rmse:0.033186+0.000711 
[12]	train-rmse:0.032094+0.000328	test-rmse:0.033171+0.000697 
[13]	train-rmse:0.032041+0.000340	test-rmse:0.033178+0.000698 
Stopping. Best iteration:
[10]	train-rmse:0.03

In [ ]:
### LASSO for instrument Selection
# names of weather and shiftshare instruments
#weather_instruments1    <- str_c('(', str_c(colnames(panel)[str_detect(colnames(panel), 'alter_[pt][rm][ca][px]..\\.r')], collapse = ' + '), ')', collapse = '')
#weather_instruments2    <- str_c('(', str_c(colnames(panel)[str_detect(colnames(panel), 'alter_[pt][rm][ca][px].._X_EgoSH\\.r')], collapse = ' + '), ')', collapse = '')
#weather_instruments3    <- str_c('(', str_c(colnames(panel)[str_detect(colnames(panel), 'alter_[pt][rm][ca][px].._Xsh\\.r')], collapse = ' + '), ')', collapse = '')
#weather_instruments4    <- str_c('(', str_c(colnames(panel)[str_detect(colnames(panel), 'alter_[pt][rm][ca][px].._Xsh_X_EgoSH\\.r')], collapse = ' + '), ')', collapse = '')
#shiftshare_instruments1 <- str_c('(', str_c(colnames(panel)[str_detect(colnames(panel), 'alter_shiftshare_..\\.r')], collapse = ' + '), ')', collapse = '')
#shiftshare_instruments2 <- str_c('(', str_c(colnames(panel)[str_detect(colnames(panel), 'alter_shiftshare_.._X_EgoSH\\.r')], collapse = ' + '), ')', collapse = '')
#shiftshare_instruments3 <- str_c('(', str_c(colnames(panel)[str_detect(colnames(panel), 'alter_shiftshare_.._Xsh\\.r')], collapse = ' + '), ')', collapse = '')
#shiftshare_instruments4 <- str_c('(', str_c(colnames(panel)[str_detect(colnames(panel), 'alter_shiftshare_.._Xsh_X_EgoSH\\.r')], collapse = ' + '), ')', collapse = '')

In [55]:
saveRDS(panel, file = '/nfs/sloanlab004/projects/covid_mobility_proj/data/PROCESSED_DATA/data_ego_alter_interactions.RData')

In [10]:
weather_instruments1    <- str_c('(', str_c(colnames(panel)[str_detect(colnames(panel), 'alter_[pt][rm][ca][px]..$')], collapse = ' + '), ')', collapse = '')
shiftshare_instruments1 <- str_c('(', str_c(colnames(panel)[str_detect(colnames(panel), 'alter_shiftshare_..$')], collapse = ' + '), ')', collapse = '')


X <- model.matrix(as.formula(str_c('PRCP ~ 0 + ', weather_instruments1 , ' * ', shiftshare_instruments1, ' * alter_sh - alter_sh')), data = panel)
X <- as.data.frame(X)

X.r <- foreach(i = 1:ncol(X), .combine = cbind) %do% XGresidualizer(X[[i]], colnames(X)[i])

[1] "alter_prcp10"
[1]	train-rmse:0.279460+0.000763	test-rmse:0.279549+0.003218 
Multiple eval metrics are present. Will use test_rmse for early stopping.
Will train until test_rmse hasn't improved in 3 rounds.

[2]	train-rmse:0.171807+0.000370	test-rmse:0.172748+0.002160 
[3]	train-rmse:0.130789+0.000854	test-rmse:0.132459+0.000880 
[4]	train-rmse:0.117300+0.000802	test-rmse:0.119539+0.000810 
[5]	train-rmse:0.112954+0.000646	test-rmse:0.115590+0.001502 
[6]	train-rmse:0.111631+0.000619	test-rmse:0.114544+0.001934 
[7]	train-rmse:0.110905+0.000732	test-rmse:0.113932+0.002043 
[8]	train-rmse:0.110192+0.001021	test-rmse:0.113276+0.002173 
[9]	train-rmse:0.109686+0.000809	test-rmse:0.113028+0.002175 
[10]	train-rmse:0.109416+0.000805	test-rmse:0.113152+0.002173 
[11]	train-rmse:0.108770+0.000895	test-rmse:0.113077+0.002142 
[12]	train-rmse:0.108566+0.000973	test-rmse:0.113132+0.002164 
Stopping. Best iteration:
[9]	train-rmse:0.109686+0.000809	test-rmse:0.113028+0.002175

[1] "alter_prcp

In [24]:
panel %>% 
    select(matches('^shiftshare_..$')) -> shiftshare
shiftshare.r <- foreach(i = 1:ncol(shiftshare), .combine = cbind) %do% XGresidualizer(shiftshare[[i]], colnames(shiftshare)[i])

[1] "shiftshare_11"
[1]	train-rmse:0.250150+0.000000	test-rmse:0.250150+0.000000 
Multiple eval metrics are present. Will use test_rmse for early stopping.
Will train until test_rmse hasn't improved in 3 rounds.

[2]	train-rmse:0.125150+0.000000	test-rmse:0.125150+0.000000 
[3]	train-rmse:0.062612+0.000000	test-rmse:0.062612+0.000000 
[4]	train-rmse:0.031325+0.000000	test-rmse:0.031325+0.000000 
[5]	train-rmse:0.015672+0.000000	test-rmse:0.015672+0.000000 
[6]	train-rmse:0.007841+0.000000	test-rmse:0.007841+0.000000 
[7]	train-rmse:0.003923+0.000000	test-rmse:0.003923+0.000000 
[8]	train-rmse:0.001963+0.000000	test-rmse:0.001963+0.000000 
[9]	train-rmse:0.000982+0.000000	test-rmse:0.000982+0.000000 
[10]	train-rmse:0.000491+0.000000	test-rmse:0.000491+0.000000 
[11]	train-rmse:0.000246+0.000000	test-rmse:0.000246+0.000000 
[12]	train-rmse:0.000123+0.000000	test-rmse:0.000124+0.000000 
[13]	train-rmse:0.000062+0.000000	test-rmse:0.000063+0.000000 
[14]	train-rmse:0.000033+0.000000	test-

In [31]:
panel %>%
    select(stay_home.r,
           alter_sh.r,
           geo_alter_sh.r,
           ban_gmr.r,
           alter_bgmr.r,
           geo_alter_bgmr.r) %>%
    bind_cols(shiftshare.r) -> residualizer_df2

exogVar_residualizer <- function(Y, colname) {
    residualizer_df2 %>%
        mutate(Y = Y) -> temp_df
    
    fit <- lm(Y ~ shiftshare_11.r + shiftshare_21.r + shiftshare_22.r + shiftshare_23.r + shiftshare_31.r + 
                  shiftshare_32.r + shiftshare_42.r + shiftshare_44.r + shiftshare_45.r + shiftshare_48.r + 
                  shiftshare_49.r + shiftshare_51.r + shiftshare_52.r + shiftshare_53.r + shiftshare_54.r + 
                  shiftshare_55.r + shiftshare_56.r + shiftshare_61.r + shiftshare_62.r + shiftshare_71.r + 
                  shiftshare_72.r + shiftshare_81.r + shiftshare_92.r + shiftshare_NA.r + ban_gmr.r + 
                  alter_bgmr.r + geo_alter_bgmr.r + stay_home.r + alter_sh.r + geo_alter_sh.r, temp_df)
    out <- data.frame(fit$resid)
    colnames(out)[1] <- colname
    return(out)
}
X.r2 <- foreach(i = 1:ncol(X.r), .combine = cbind) %dopar% exogVar_residualizer(X.r[[i]], colnames(X.r)[i])           

In [32]:
panel %>% 
    select(alter_nhd.r,
           alter_mcbgv.r,
           alter_rnstu.r,
           alter_btvrc.r,
           ash_alter_nhd.r,
           log_alter_mcbgv.r,
           ash_alter_rnstu.r) -> DVs

Y <- foreach(i = 1:ncol(DVs), .combine = cbind) %dopar% exogVar_residualizer(DVs[[i]], colnames(DVs)[i])         

In [35]:
# Running cross-validated lasso, to select optimal lambda (based on CV prediction performance)
X.r2 <- as.matrix(X.r2)
Y    <- as.matrix(Y)


cvlasso <- cv.glmnet(X.r2, Y, 
                     intercept = FALSE,
                     family = 'mgaussian',
                     alpha = 1,
                     weights = panel$n,
                     foldid = panel$grp,
                     standardize = FALSE,
                     parallel = TRUE,
                     nlambda = 100)

# Extracting selected instruments]
fs.lasso.coefs <- coef(cvlasso, s = cvlasso$lambda.1se)[[1]]
selected.cols  <- which(fs.lasso.coefs != 0)
selected.names <- rownames(fs.lasso.coefs)[selected.cols]

In [38]:
fs.lasso.coefs <- coef(cvlasso, s = cvlasso$lambda.1se)[[1]]
selected.cols  <- which(fs.lasso.coefs != 0)
selected.names <- rownames(fs.lasso.coefs)[selected.cols]

In [41]:
save(cvlasso, file = '/nfs/sloanlab004/projects/covid_mobility_proj/data/PROCESSED_DATA/ivLassoModel.Rdata')

In [42]:
X.r2[, selected.names] -> instruments
ivNames <- data.frame(iv = str_c('iv', id = str_pad(1:ncol(instruments), 3, pad = '0')), var = colnames(instruments))
colnames(instruments) <- str_c('iv', str_pad(1:ncol(instruments), 3, pad = '0'))
save(ivNames, file = '/nfs/sloanlab004/projects/covid_mobility_proj/data/PROCESSED_DATA/ivNames.RData')

In [44]:
panel %>%
    select(-matches('prcp..'),
           -matches('tmax..'),
           -matches('_Xsh'),
           -matches('X_EgoSH'),
           -grp) %>%
    bind_cols(as.data.frame(instruments)) -> panel


In [ ]:
panel %>%
    select(-matches('prcp..'),
           -matches('tmax..'),
           -matches('_Xsh'),
           -matches('X_EgoSH'),
           -grp) %>%
    bind_cols(as.data.frame(instruments)) -> panel

In [45]:
saveRDS(panel, file = '/nfs/sloanlab004/projects/covid_mobility_proj/data/PROCESSED_DATA/data_v2.RData')

In [47]:
ivNames$var

[1] alter_prcp10.r                             
  [2] alter_prcp11.r                             
  [3] alter_prcp12.r                             
  [4] alter_prcp13.r                             
  [5] alter_prcp14.r                             
  [6] alter_prcp15.r                             
  [7] alter_prcp16.r                             
  [8] alter_prcp17.r                             
  [9] alter_prcp18.r                             
 [10] alter_prcp19.r                             
 [11] alter_prcp20.r                             
 [12] alter_tmax02.r                             
 [13] alter_tmax03.r                             
 [14] alter_tmax04.r                             
 [15] alter_tmax05.r                             
 [16] alter_tmax06.r                             
 [17] alter_tmax07.r                             
 [18] alter_tmax08.r                             
 [19] alter_tmax09.r                             
 [20] alter_tmax10.r                             
 [21] alter_tmax11.r                             
 [22] alter_tmax12.r                             
 [23] alter_tmax13.r                             
 [24] alter_tmax14.r                             
 [25] alter_tmax15.r                             
 [26] alter_tmax16.r                             
 [27] alter_tmax17.r                             
 [28] alter_tmax18.r                             
 [29] alter_tmax19.r                             
 [30] alter_tmax20.r                             
 [31] alter_shiftshare_31.r                      
 [32] alter_shiftshare_44.r                      
 [33] alter_shiftshare_45.r                      
 [34] alter_shiftshare_51.r                      
 [35] alter_shiftshare_52.r                      
 [36] alter_shiftshare_53.r                      
 [37] alter_shiftshare_61.r                      
 [38] alter_shiftshare_62.r                      
 [39] alter_shiftshare_71.r                      
 [40] alter_shiftshare_72.r                      
 [41] alter_shiftshare_81.r                      
 [42] alter_prcp10:alter_shiftshare_44.r         
 [43] alter_prcp10:alter_shiftshare_45.r         
 [44] alter_prcp10:alter_shiftshare_53.r         
 [45] alter_prcp10:alter_shiftshare_61.r         
 [46] alter_prcp10:alter_shiftshare_62.r         
 [47] alter_prcp10:alter_shiftshare_71.r         
 [48] alter_prcp10:alter_shiftshare_72.r         
 [49] alter_prcp10:alter_shiftshare_81.r         
 [50] alter_prcp11:alter_shiftshare_44.r         
 [51] alter_prcp11:alter_shiftshare_45.r         
 [52] alter_prcp11:alter_shiftshare_53.r         
 [53] alter_prcp11:alter_shiftshare_61.r         
 [54] alter_prcp11:alter_shiftshare_62.r         
 [55] alter_prcp11:alter_shiftshare_71.r         
 [56] alter_prcp11:alter_shiftshare_72.r         
 [57] alter_prcp12:alter_shiftshare_45.r         
 [58] alter_prcp12:alter_shiftshare_53.r         
 [59] alter_prcp12:alter_shiftshare_61.r         
 [60] alter_prcp12:alter_shiftshare_71.r         
 [61] alter_prcp12:alter_shiftshare_72.r         
 [62] alter_prcp12:alter_shiftshare_81.r         
 [63] alter_prcp13:alter_shiftshare_44.r         
 [64] alter_prcp13:alter_shiftshare_53.r         
 [65] alter_prcp13:alter_shiftshare_61.r         
 [66] alter_prcp13:alter_shiftshare_62.r         
 [67] alter_prcp13:alter_shiftshare_71.r         
 [68] alter_prcp13:alter_shiftshare_72.r         
 [69] alter_prcp14:alter_shiftshare_44.r         
 [70] alter_prcp14:alter_shiftshare_61.r         
 [71] alter_prcp14:alter_shiftshare_62.r         
 [72] alter_prcp14:alter_shiftshare_71.r         
 [73] alter_prcp14:alter_shiftshare_72.r         
 [74] alter_prcp14:alter_shiftshare_81.r         
 [75] alter_prcp15:alter_shiftshare_44.r         
 [76] alter_prcp15:alter_shiftshare_62.r         
 [77] alter_prcp15:alter_shiftshare_71.r         
 [78] alter_prcp15:alter_shiftshare_72.r         
 [79] alter_prcp16:alter_shiftshare_44.r         
 [80] alter_prcp16:alter_shiftshare_45.r         
 [

In [ ]:
colnames(panel)